In [86]:
import pandas as pd
import numpy as np
import folium
import json
from pathlib import Path
from ipyleaflet import Map, Choropleth, GeoJSON, WidgetControl
from branca.colormap import linear
import ipywidgets as widgets
import geopandas as gpd
from shapely.geometry import Polygon, Point
from shapely import wkt
from pyproj import CRS
from jinja2 import Template
from folium.map import Marker
from folium import Element, MacroElement



current_dir = Path.cwd()
parent_dir = current_dir.parent 

In [2]:
ces_df = pd.read_csv(f"{parent_dir}/cleaned_data/cleaned_ces_cdc.csv")

In [23]:
#Map centered on California
m = folium.Map(location=[37.77,-122.41], zoom_start=10)
#gemerate map
#m.save('map.html')
#m

In [59]:

geojson_path = f'{current_dir}/data/tract_boundaries.json'
with open(geojson_path) as f:
    geojson_data = json.load(f)

#Adding "id" feature to geojson file
for tract in geojson_data['features']:
    ID = tract['properties']['GEOID']
    tract['id'] = ID

#Adding tracts present in the Geojson file but not the DAC classification data as missing values
data = pd.read_csv(f"{current_dir}/cleaned_data/geo_df.csv", dtype=str)
tracts = [tract['id'] for tract in geojson_data['features']]
missing_tracts = [tract for tract in tracts if tract not in data['GEOID'].values]

#initializing datagrame for missing tracts
missing_df = pd.DataFrame()
missing_df['GEOID'] = missing_tracts
for col in data.columns[1:]:
    missing_df[col] = np.repeat(None, len(missing_tracts))

#Appending missing tracts to DAC dataframe
new_df = pd.concat([data, missing_df], ignore_index=True)

#Classifying missing tracts as "missing"
def categorize(col):
    if col == '1':
        return 'Yes'
    elif col == '0':
        return 'No'
    else: 
        return "Missing"
new_df['DAC'] = new_df['DAC'].apply(categorize)
new_df.to_csv(f"{current_dir}/cleaned_data/geo_df.csv", index=False)




for tract in geojson_data['features']:
    ID = tract['properties']['GEOID']
    tract['DAC'] = new_df.loc[new_df['GEOID'] == ID]['DAC'].values[0]
    tract['id'] = ID
    prop = {}
    count = 0
    for key, val in tract['properties'].items():
        if count <= 4:
            prop[key] = val
            count +=1
    tract['properties'] = prop

fp = f'{current_dir}/cleaned_data/tract_boundaries.json'
with open(fp, 'w') as file:
    json.dump(geojson_data, file, indent=4)

In [63]:
dac_data = pd.read_csv(f"{current_dir}/cleaned_data/default_score.csv")
dac_data

Census Tract        County  env_exposure  env_effect   sens_pop  \
0       6019001100        Fresno      81.90625      73.124  95.030000   
1       6077000700   San Joaquin      63.92500      92.456  90.353333   
2       6037204920   Los Angeles      76.37375      80.272  87.933333   
3       6019000700        Fresno      72.33000      58.882  97.530000   
4       6019000200        Fresno      80.54875      39.380  97.423333   
...            ...           ...           ...         ...        ...   
7927    6081609700     San Mateo      24.14000       3.328   6.356667   
7928    6085507302   Santa Clara      21.20625      23.588   4.450000   
7929    6013351200  Contra Costa      24.24750      22.760   4.930000   
7930    6081609601     San Mateo      14.71500       0.360   9.250000   
7931    6041126100         Marin      25.19500      25.168   3.733333   

      ses_factors  Pollution Burden   Pop Char  Pollution Burden MinMax  \
0          91.278         78.978833  93.154000                 9.643207   
1          95.976         73.435333  93.164667                 8.966354   
2          79.566         77.673167  83.749667                 9.483787   
3          91.752         67.847333  94.641000                 8.284067   
4          93.376         66.825833  95.399667                 8.159343   
...           ...               ...        ...                      ...   
7927        5.994         17.202667   6.175333                 2.100422   
7928        4.918         22.000167   4.684000                 2.686190   
7929        3.370         23.751667   4.150000                 2.900046   
7930        8.164          9.930000   8.707000                 1.212439   
7931        2.744         25.186000   3.238667                 3.075176   

      Pop Char MinMax      Score  Percentile  DAC  
0            9.663153  93.183786  100.000000    1  
1            9.664259  86.653166   99.987393    1  
2            8.687612  82.391466   99.974786    1  
3            9.817404  81.328026   99.962179    1  
4            9.896103  80.745694   99.949571    1  
...               ...        ...         ...  ...  
7927         0.640586   1.345502    0.063036    0  
7928         0.485886   1.305182    0.050429    0  
7929         0.430492   1.248448    0.037821    0  
7930         0.903204   1.095080    0.025214    0  
7931         0.335957   1.033127    0.012607    0  

[7932 rows x 13 columns]

In [3]:
#Load the Data
geojson_path = f'{current_dir}/data/tract_boundaries.json'
with open(geojson_path) as f:
    geojson_data = json.load(f)

def style_function(feature):
    return {
        'fillColor': '#ffaf00',  # Fill color (hex color code)
        'color': 'black',         # Border color
        'weight': 0.5,             # Border width
        'fillOpacity': 0,      # Fill opacity
    }

m = folium.Map(location=[37.77,-122.41], zoom_start=10)
folium.GeoJson(geojson_data,
               style_function=style_function).add_to(m)
#m

In [67]:
##Working code, Could alter the color scheme
#Actually, broke somewhat after changing the geo_df.csv generation process. Is likely due to either changing the 
#DAC classifications from integers to strings or the inclusion of tracts with missing
geojson_path = f'{current_dir}/data/tract_boundaries.json'
with open(geojson_path) as f:
    geojson_data = json.load(f)

data = pd.read_csv(f"{current_dir}/cleaned_data/geo_df.csv")

def style_function(feature):
    return {
        'fillColor': '#ffaf00',  # Fill color (hex color code)
        'color': 'black',         # Border color
        'weight': 0.5,             # Border width
        'fillOpacity': 0,      # Fill opacity
    }

m = folium.Map(location=[37.77,-122.41], zoom_start=6)

folium.Choropleth(
    geo_data=geojson_data,
    data=data,
    columns=['GEOID', 'DAC'],
    key_on='properties.GEOID',
    fill_color='GnBu',
    fill_opacity=0.5,
    line_opacity=0.5,
    legend_name='DAC_Designated'
).add_to(m)
m.save(f'{current_dir}/Static/html/original_map.html')


TypeError: ufunc 'isnan' not supported for the input types, and the inputs could not be safely coerced to any supported types according to the casting rule ''safe''

In [3]:
# Load the GeoJSON data
#geojson_path = f'{current_dir}/cleaned_data/tract_boundaries.json'
with open(geojson_path) as f:
    geojson_data = json.load(f)


#Colors for each DAC category
colors = {
    'Yes': ['#2EEC57', 0.7],
    'No': ['#EC2E42', 0.7],
    'Missing': ['#C0C0C0', 0.5]
}

# Function to style the GeoJSON layer
def style_function(feature):
    return {
        'fillColor': colors[feature['DAC']][0],  # Fill color (hex color code)
        'color': 'black',        # Border color
        'weight': 0.1,           # Border width
        'fillOpacity': colors[feature['DAC']][1]         # Fill opacity
    }


# Create a map
m = folium.Map(location=[37.77,-122.41], zoom_start=6)

# Create a GeoJSON layer
geo_json_layer = folium.GeoJson(
    data=geojson_data,
    style_function=style_function,
    #highlight_function={'fillColor': 'yellow', 'fillOpacity': 0.2},
    name='DAC Classification'
).add_to(m)

# Add the GeoJSON layer to the map
folium.LayerControl().add_to(m)


#m.save(f'{current_dir}/Static/original_map.html')

# Display the map
#m

NameError: name 'geojson_path' is not defined

In [44]:
#Adding tracts present in the Geojson file but not the DAC classification data as missing values

data = pd.read_csv(f"{current_dir}/cleaned_data/geo_df.csv", dtype=str)
data.loc[data['GEOID'] == '06085504321']
tracts = [tract['id'] for tract in geojson_data['features']]
missing_tracts = [tract for tract in tracts if tract not in data['GEOID'].values]
#missing_tracts = np.array([[tract, None, None, None, None, None, None, None, None, None, None, None] for tract in tracts])
missing_df = pd.DataFrame()
missing_df['GEOID'] = missing_tracts
for col in data.columns[1:]:
    missing_df[col] = np.repeat(None, len(missing_tracts))
new_df = pd.concat([data, missing_df], ignore_index=True)
new_df
def categorize(col):
    if col == '1':
        return 'Yes'
    elif col == '0':
        return 'No'
    else: 
        return "Missing"
new_df['DAC'] = new_df['DAC'].apply(categorize)
new_df.to_csv(f"{current_dir}/cleaned_data/geo_df.csv", index=False)

In [9]:
fp = f'{parent_dir}/cleaned_data/tract_boundaries.json'
with open(fp) as f:
    geojson_data = json.load(f)
geodf = gpd.read_file(fp)



In [4]:
#geojson_data['features'][0]
codes = pd.read_csv(f"{parent_dir}/data/CA_County_Codes.csv")
rel_df = ces_df[['Census Tract','County']].copy()
geodf

id STATEFP COUNTYFP TRACTCE        GEOID     NAME  \
0     06085504321      06      085  504321  06085504321  5043.21   
1     06085504410      06      085  504410  06085504410  5044.10   
2     06085507003      06      085  507003  06085507003  5070.03   
3     06085507004      06      085  507004  06085507004  5070.04   
4     06085502204      06      085  502204  06085502204  5022.04   
...           ...     ...      ...     ...          ...      ...   
9124  06059001303      06      059  001303  06059001303    13.03   
9125  06059001304      06      059  001304  06059001304    13.04   
9126  06059001401      06      059  001401  06059001401    14.01   
9127  06013367200      06      013  367200  06013367200     3672   
9128  06037578100      06      037  578100  06037578100     5781   

                                               geometry  
0     POLYGON ((-121.87556 37.39924, -121.87541 37.3...  
1     POLYGON ((-121.88886 37.40758, -121.88813 37.4...  
2     POLYGON ((-122.00238 37.24149, -122.00264 37.2...  
3     POLYGON ((-121.98458 37.23129, -121.98498 37.2...  
4     POLYGON ((-121.93167 37.29803, -121.93166 37.2...  
...                                                 ...  
9124  POLYGON ((-117.95917 33.92458, -117.95917 33.9...  
9125  POLYGON ((-117.95918 33.9282, -117.95918 33.92...  
9126  POLYGON ((-117.95046 33.94607, -117.95045 33.9...  
9127  POLYGON ((-122.34415 37.9674, -122.34463 37.96...  
9128  POLYGON ((-118.12345 33.78715, -118.12343 33.7...  

[9129 rows x 7 columns]

In [10]:


#Colors for each DAC category
colors = {
    'Yes': ['#2EEC57', 0.7],
    'No': ['#EC2E42', 0.7],
    'Missing': ['#C0C0C0', 0.5]
}

# Function to style the GeoJSON layer
def style_function(feature):
    return {
        'fillColor': colors[feature['DAC']][0],  # Fill color (hex color code)
        'color': 'black',        # Border color
        'weight': 0.1,           # Border width
        'fillOpacity': colors[feature['DAC']][1]         # Fill opacity
    }


# Create a map
m = folium.Map(location=[37.77,-122.41], zoom_start=6)

# Create a GeoJSON layer
geo_json_layer = folium.GeoJson(
    data=geojson_data,
    style_function=style_function,
    #highlight_function={'fillColor': 'yellow', 'fillOpacity': 0.2},
    name='DAC Classification'
).add_to(m)

# Add the GeoJSON layer to the map
folium.LayerControl().add_to(m)


m.save(f'{parent_dir}/Static/original_map.html')

# Display the map
m

In [29]:
print(geojson_data['features'][0])
gdf_components = {
    'tract': [],
    'county': [],
    'DAC': [],
    'party': [],
    'geometry': [],
}
for tract in geojson_data['features']:
    new_tract = {}
    trid = int(tract['id'][1:])
    gdf_components['tract'].append(trid)
    new_tract['geometry'] = tract['geometry']['coordinates']
    gdf_components['geometry'].append(tract['geometry']['coordinates'])
    new_tract['id'] = trid
    if tract['DAC'] == 'No':
        new_tract['DAC'] = 0
        gdf_components['DAC'].append(0)
    if tract['DAC'] == 'Yes':
        new_tract['DAC'] = 1
        gdf_components['DAC'].append(1)
    if tract['DAC'] == 'Missing':
        new_tract['DAC'] = -1
        gdf_components['DAC'].append(-1)
    try:
        party = ces_df.loc[ces_df['Census Tract'] == trid]['Party'].values[0][0]
        county = ces_df.loc[ces_df['Census Tract'] == trid]['County'].values[0]
    except:
        party = 'M'
        county = 'M'
    #print(trid)
    new_tract['party'] = party
    gdf_components['party'].append(party)
    new_tract['county'] = county
    gdf_components['county'].append(county)

gdf_components


{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[-121.875559, 37.39924], [-121.875412, 37.398811], [-121.875, 37.397665], [-121.874826, 37.397166], [-121.874611, 37.396693], [-121.874331, 37.396144], [-121.874051, 37.395627], [-121.873808, 37.395275], [-121.873314, 37.394571], [-121.872745, 37.39388], [-121.87203, 37.393108], [-121.871461, 37.392628], [-121.87036, 37.391566], [-121.870054, 37.39127], [-121.868446, 37.389771], [-121.866786, 37.388198], [-121.866184, 37.387661], [-121.865445, 37.387002], [-121.863054, 37.384864], [-121.862864, 37.38467], [-121.862772, 37.384754], [-121.862462, 37.38508], [-121.86203, 37.385528], [-121.861778, 37.38579], [-121.861533, 37.385993], [-121.861125, 37.386287], [-121.860774, 37.386531], [-121.860561, 37.386558], [-121.860266, 37.386774], [-121.860226, 37.386804], [-121.859988, 37.38699], [-121.859833, 37.387138], [-121.859657, 37.387339], [-121.85952, 37.387538], [-121.859398, 37.387722], [-121.859371, 37.387765], [-121.859

{'tract': [6085504321,
  6085504410,
  6085507003,
  6085507004,
  6085502204,
  6085502203,
  6085501902,
  6085502104,
  6085502103,
  6085504424,
  6085505015,
  6085505012,
  6085505014,
  6085505010,
  6085501901,
  6085511502,
  6085504903,
  6085504808,
  6085511501,
  6085512057,
  6085512059,
  6085503339,
  6085503338,
  6085512056,
  6085503219,
  6085503222,
  6085509111,
  6085507705,
  6085507704,
  6085512058,
  6085504807,
  6085508205,
  6085508510,
  6085508206,
  6085512513,
  6085512512,
  6085512514,
  6085512516,
  6085508305,
  6085504509,
  6085501601,
  6085501602,
  6085506505,
  6085504510,
  6085508708,
  6085505902,
  6085503127,
  6085503126,
  6085503124,
  6085503125,
  6085512055,
  6085509002,
  6085509001,
  6085508306,
  6085502704,
  6059062651,
  6059062650,
  6059062654,
  6059052531,
  6059052532,
  6059032063,
  6059062658,
  6059042341,
  6059042115,
  6059075517,
  6059052437,
  6059052534,
  6059052430,
  6059052434,
  6059075516,
  605907551

In [10]:
fp = f'{parent_dir}/cleaned_data/tract_boundaries.json'
with open(fp) as f:
    geojson_data = json.load(f)

In [45]:
geojson_data['features'][0].keys()
geojson_data['features'][0]['properties']

{'STATEFP': '06',
 'COUNTYFP': '085',
 'TRACTCE': '504321',
 'GEOID': '06085504321',
 'NAME': '5043.21',
 'NAMELSAD': 'Census Tract 5043.21',
 'MTFCC': 'G5020',
 'FUNCSTAT': 'S',
 'ALAND': 1450237,
 'AWATER': 0,
 'INTPTLAT': '+37.3931319',
 'INTPTLON': '-121.8651427'}

In [11]:
geojson_df = gpd.read_file(fp)
geojson_df

id STATEFP COUNTYFP TRACTCE        GEOID     NAME  \
0     06085504321      06      085  504321  06085504321  5043.21   
1     06085504410      06      085  504410  06085504410  5044.10   
2     06085507003      06      085  507003  06085507003  5070.03   
3     06085507004      06      085  507004  06085507004  5070.04   
4     06085502204      06      085  502204  06085502204  5022.04   
...           ...     ...      ...     ...          ...      ...   
9124  06059001303      06      059  001303  06059001303    13.03   
9125  06059001304      06      059  001304  06059001304    13.04   
9126  06059001401      06      059  001401  06059001401    14.01   
9127  06013367200      06      013  367200  06013367200     3672   
9128  06037578100      06      037  578100  06037578100     5781   

                                               geometry  
0     POLYGON ((-121.87556 37.39924, -121.87541 37.3...  
1     POLYGON ((-121.88886 37.40758, -121.88813 37.4...  
2     POLYGON ((-122.00238 37.24149, -122.00264 37.2...  
3     POLYGON ((-121.98458 37.23129, -121.98498 37.2...  
4     POLYGON ((-121.93167 37.29803, -121.93166 37.2...  
...                                                 ...  
9124  POLYGON ((-117.95917 33.92458, -117.95917 33.9...  
9125  POLYGON ((-117.95918 33.9282, -117.95918 33.92...  
9126  POLYGON ((-117.95046 33.94607, -117.95045 33.9...  
9127  POLYGON ((-122.34415 37.9674, -122.34463 37.96...  
9128  POLYGON ((-118.12345 33.78715, -118.12343 33.7...  

[9129 rows x 7 columns]

In [12]:
county_boundaries = gpd.read_file(f"{parent_dir}/data/ca_counties/CA_Counties.shp")
county_bdr = county_boundaries[['COUNTYFP', 'NAME']]
county_bdr

COUNTYFP             NAME
0       091           Sierra
1       067       Sacramento
2       083    Santa Barbara
3       009        Calaveras
4       111          Ventura
5       037      Los Angeles
6       097           Sonoma
7       031            Kings
8       073        San Diego
9       061           Placer
10      075    San Francisco
11      041            Marin
12      043         Mariposa
13      035           Lassen
14      055             Napa
15      089           Shasta
16      053         Monterey
17      105          Trinity
18      045        Mendocino
19      027             Inyo
20      051             Mono
21      109         Tuolumne
22      095           Solano
23      071   San Bernardino
24      013     Contra Costa
25      003           Alpine
26      017        El Dorado
27      113             Yolo
28      115             Yuba
29      069       San Benito
30      023         Humboldt
31      065        Riverside
32      029             Kern
33      011           Colusa
34      015        Del Norte
35      049            Modoc
36      019           Fresno
37      039           Madera
38      085      Santa Clara
39      103           Tehama
40      077      San Joaquin
41      001          Alameda
42      057           Nevada
43      007            Butte
44      047           Merced
45      107           Tulare
46      099       Stanislaus
47      059           Orange
48      025         Imperial
49      101           Sutter
50      005           Amador
51      033             Lake
52      063           Plumas
53      081        San Mateo
54      093         Siskiyou
55      087       Santa Cruz
56      021            Glenn
57      079  San Luis Obispo

In [13]:
geodf2 = geodf[['id', 'COUNTYFP', 'geometry']].copy()
geodf3 = geodf2.merge(county_bdr, how='left', on='COUNTYFP').rename(columns={'COUNTYFP': 'county_code', 'NAME': 'County'})
geodf3

id county_code  \
0     06085504321         085   
1     06085504410         085   
2     06085507003         085   
3     06085507004         085   
4     06085502204         085   
...           ...         ...   
9124  06059001303         059   
9125  06059001304         059   
9126  06059001401         059   
9127  06013367200         013   
9128  06037578100         037   

                                               geometry        County  
0     POLYGON ((-121.87556 37.39924, -121.87541 37.3...   Santa Clara  
1     POLYGON ((-121.88886 37.40758, -121.88813 37.4...   Santa Clara  
2     POLYGON ((-122.00238 37.24149, -122.00264 37.2...   Santa Clara  
3     POLYGON ((-121.98458 37.23129, -121.98498 37.2...   Santa Clara  
4     POLYGON ((-121.93167 37.29803, -121.93166 37.2...   Santa Clara  
...                                                 ...           ...  
9124  POLYGON ((-117.95917 33.92458, -117.95917 33.9...        Orange  
9125  POLYGON ((-117.95918 33.9282, -117.95918 33.92...        Orange  
9126  POLYGON ((-117.95046 33.94607, -117.95045 33.9...        Orange  
9127  POLYGON ((-122.34415 37.9674, -122.34463 37.96...  Contra Costa  
9128  POLYGON ((-118.12345 33.78715, -118.12343 33.7...   Los Angeles  

[9129 rows x 4 columns]

In [43]:
current_dir = parent_dir

##Loading files
#Tract boundary geojson file
geojson_path = f'{current_dir}/data/tract_boundaries.json'
with open(geojson_path) as f:
    geojson_data = json.load(f)
geojson_df = gpd.read_file(geojson_path)

#Default score and percentiles generated by process_data.py
dac_data = pd.read_csv(f"{current_dir}/cleaned_data/default_score.csv")
#The full calenviroscreen data table generated by process_data/py
ces_df = pd.read_csv(f"{current_dir}/cleaned_data/cleaned_ces_cdc.csv")
#Shapefile containing CA district boundaries
district_df = gpd.read_file(f"{current_dir}/data/ca_assembly_districts/Assembly_Districts.shp")
#csv containing district party affiliations
party_data = pd.read_csv(f"{current_dir}/data/california_state_assembly_district_parties_03_23.csv")
county_df = gpd.read_file(f"{parent_dir}/data/ca_counties/CA_Counties.shp")

In [44]:

#Removing unnecessary columns and adding Leading zero to census tracts (to match GEOjson file)
dac_data.drop(columns=dac_data.columns[2:-3], inplace=True)
dac_data.rename(columns={'Census Tract': "GEOID"}, inplace=True)
def leading_zero(col):
    return '0' + str(col)
dac_data['GEOID'] = dac_data['GEOID'].apply(leading_zero)

#Adding tracts present in the Geojson file but not the DAC classification data as missing values
tracts = [tract['properties']['GEOID'] for tract in geojson_data['features']]
missing_tracts = [tract for tract in tracts if tract not in dac_data['GEOID'].values]

#initializing dataframe for missing tracts
missing_df = pd.DataFrame()
missing_df['GEOID'] = missing_tracts
for col in dac_data.columns[1:]:
    missing_df[col] = np.repeat(None, len(missing_tracts))

#Appending missing tracts to DAC dataframe
dac_data_complete = pd.concat([dac_data, missing_df], ignore_index=True)

#Classifying missing tracts as "missing"
def categorize(col):
    if col == 1:
        return 'Yes'
    elif col == 0:
        return 'No'
    else: 
        return "Missing"
dac_data_complete['DAC'] = dac_data_complete['DAC'].apply(categorize)

polygons = []
tract_ids = []
counties = []
#Adding a DAC and an id element to the geojson file and removing unnecessary properties
#Additionally, reducing polygon size
for tract in geojson_data['features']:
    ID = tract['properties']['GEOID']
    county_code = tract['properties']['COUNTYFP']
    county = county_df.loc[county_df['COUNTYFP'] == county_code]['NAME'].values[0]
    #tract['DAC'] = dac_data_complete.loc[dac_data_complete['GEOID'] == ID]['DAC'].values[0]
    #tract['id'] = ID
    prop = {
        'id': ID,
        'county': county,
        'DAC': dac_data_complete.loc[dac_data_complete['GEOID'] == ID]['DAC'].values[0]
    }
    tract['properties'] = prop
    try:
        def reduce_polygon(poly_list):
            poly_reduced = poly_list[::2]
            return Polygon(poly_reduced)
        poly_complex = tract['geometry']['coordinates'][0]
        polygon_reduced = reduce_polygon(poly_complex)
        #tract['geometry']['coordinates'] = polygon_reduced
    except:
        polygon_reduced = 'None'
        ID = 'None'
        county = 'None'
    polygons.append(polygon_reduced)
    tract_ids.append(ID)
    counties.append(county)

#Creating a geo dataframe with census tract areas
polygons_clean = [x for x in polygons if x != 'None']
ids_clean = [x for x in tract_ids if x != 'None']
counties_clean = [x for x in counties if county != 'None']
area_df = gpd.GeoDataFrame(geometry=polygons_clean, crs=CRS.from_epsg(4326))

#Creating a geodataframe with geometry, DAC classification, and county name
geojson_df2 = geojson_df[['COUNTYFP', 'GEOID']].copy()
county_df2 = county_df[['COUNTYFP', 'NAME']].copy()
tract_county_merged = geojson_df2.merge(county_df2, how='left', on='COUNTYFP')
tract_county_df = dac_data_complete.merge(tract_county_merged, how='left', on='GEOID').drop(
    columns=['COUNTYFP', 'Score', 'Percentile', 'County']).rename(columns={'NAME': 'County'})
basic_geojson_df = area_df.copy()
basic_geojson_df['id'] = ids_clean
basic_geojson_df = basic_geojson_df.merge(tract_county_df, how='left', left_on='id', right_on='GEOID')

area_df['GEOID'] = ids_clean
#Converting to a Califoria CRS
area_df = area_df.to_crs(CRS.from_epsg(3310))
area_df['area'] = area_df.area
area_df['area'] = area_df['area'].apply(lambda x: round(x, 2))

def remove_zero(num):
    return int(num[1:])

area_df['GEOID'] = area_df['GEOID'].apply(remove_zero)
dac_data_complete['GEOID'] = dac_data_complete['GEOID'].apply(remove_zero)

#Merging area dataframe with classificaion dataframe
geo_merged = dac_data_complete.merge(area_df, on='GEOID', how='outer').drop(columns=['geometry'])

#Adding population density to calenviroscreen data
ces_df3 = ces_df.merge(geo_merged, left_on='Census Tract', right_on='GEOID', how='left').drop(
    columns=['County_y', 'Score', 'Percentile', 'DAC', 'GEOID', 'County_x']).rename(columns={'California County': 'County'})
ces_df3['Population Density'] = ces_df3['Total Population'] / ces_df3['area'] * 1000

## Adding political affiliation to calenviroscreen data
tract_df = ces_df[['Census Tract', 'Longitude', 'Latitude']]
def make_point(row):
    return Point(row[-2], row[-1])

#Adding (long,lat) gemoetry to ces census tracts
tract_df['geometry'] = tract_df.apply(make_point, axis=1)
tract_df = gpd.GeoDataFrame(tract_df, geometry='geometry', crs="EPSG:4326").drop(columns=['Latitude','Longitude'])
tract_df.to_crs(district_df.crs, inplace=True)

#Classifying census tracts into their corresponding districts
tract_districts = gpd.sjoin(tract_df, district_df, how='left', predicate='within')
def remove_leading_zero(val):
    try:
        if val[0] == '0':
            val = val[1:]
        return val
    except:
        return val
    
party_data['District'] = party_data['District'].apply(str)
tract_districts['GEOID'] = tract_districts['GEOID'].apply(remove_leading_zero)
#Merging census tracts with party affiliation data
tract_districts2 = tract_districts.merge(party_data, left_on='GEOID', right_on='District', 
                      how='left').drop(columns=['index_right','AssemblyAr','District','Assembly_1',
                                                'District','Name', 'AssemblyDi'])
tract_districts = tract_districts.merge(party_data, left_on='GEOID', right_on='District', 
                      how='left').drop(columns=['geometry','index_right','GEOID','AssemblyAr','District','Assembly_1',
                                                'District','Name', 'AssemblyDi'])

ces_df3 = ces_df3.merge(tract_districts, on='Census Tract')

#Saving geojson file
fp = f'{current_dir}/cleaned_data/tract_boundaries.json'
with open(fp, 'w') as file:
    json.dump(geojson_data, file)

#Saving altered dac data file
geo_merged.to_csv(f"{current_dir}/cleaned_data/geo_df.csv", index=False)

#Saving altered calenviroscreen data
ces_df3.to_csv(f"{current_dir}/cleaned_data/cleaned_ces_cdc.csv", index=False)

#Saving geopandas data
basic_geojson_df.to_csv(f"{current_dir}/cleaned_data/geojson_data.csv")

C:\Users\cflor\AppData\Local\Temp\ipykernel_34656\2469376097.py:25: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  dac_data_complete = pd.concat([dac_data, missing_df], ignore_index=True)
C:\Users\cflor\AppData\Local\Temp\ipykernel_34656\2469376097.py:108: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return Point(row[-2], row[-1])
C:\Users\cflor\AppData\Local\Temp\ipykernel_34656\2469376097.py:111: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the cav

In [42]:
geojson_df2 = geojson_df[['COUNTYFP', 'GEOID']].copy()
county_df2 = county_df[['COUNTYFP', 'NAME']].copy()
tract_county_merged = geojson_df2.merge(county_df2, how='left', on='COUNTYFP')
tract_county_df = dac_data_complete.merge(tract_county_merged, how='left', on='GEOID').drop(
    columns=['COUNTYFP', 'Score', 'Percentile', 'County']).rename(columns={'NAME': 'County'})

basic_geojson_df.merge(tract_county_df, how='left', left_on='id', right_on='GEOID')

geometry           id  \
0     POLYGON ((-121.87556 37.39924, -121.875 37.397...  06085504321   
1     POLYGON ((-121.88886 37.40758, -121.88797 37.4...  06085504410   
2     POLYGON ((-122.00238 37.24149, -122.00313 37.2...  06085507003   
3     POLYGON ((-121.98458 37.23129, -121.98549 37.2...  06085507004   
4     POLYGON ((-121.93167 37.29803, -121.93167 37.2...  06085502204   
...                                                 ...          ...   
9110  POLYGON ((-117.95917 33.92458, -117.95917 33.9...  06059001303   
9111  POLYGON ((-117.95918 33.9282, -117.95918 33.92...  06059001304   
9112  POLYGON ((-117.95046 33.94607, -117.95044 33.9...  06059001401   
9113  POLYGON ((-122.34415 37.9674, -122.34494 37.96...  06013367200   
9114  POLYGON ((-118.12345 33.78715, -118.12341 33.7...  06037578100   

            GEOID      DAC        County  
0     06085504321       No   Santa Clara  
1     06085504410       No   Santa Clara  
2     06085507003  Missing   Santa Clara  
3     06085507004  Missing   Santa Clara  
4     06085502204  Missing   Santa Clara  
...           ...      ...           ...  
9110  06059001303       No        Orange  
9111  06059001304      Yes        Orange  
9112  06059001401      Yes        Orange  
9113  06013367200       No  Contra Costa  
9114  06037578100  Missing   Los Angeles  

[9115 rows x 5 columns]

In [60]:
df = pd.read_csv(f'{parent_dir}/cleaned_data/geojson_data.csv')
df['geometry'] = df['geometry'].apply(wkt.loads)
geo_df = gpd.GeoDataFrame(df, geometry='geometry')

In [79]:
#Colors for each DAC category


colors = {
    'Yes': ['#2EEC57', 0.7],
    'No': ['#EC2E42', 0.7],
    'Missing': ['#C0C0C0', 0.5]
}

geo_df2 = geo_df.loc[geo_df['County'] == 'Los Angeles']

# Function to style the GeoJSON layer
def style_function(feature):
    category = feature['properties']['DAC']
    return {
        'fillColor': colors[category][0],  # Fill color (hex color code)
        'color': 'black',        # Border color
        'weight': 0.1,           # Border width
        'fillOpacity': colors[category][1]         # Fill opacity
    }

long, lat = list(geo_df2['geometry'].values[4].exterior.coords)[0]

# Create a map
m = folium.Map(location=[lat, long], zoom_start=8)

# Create a GeoJSON layer
geo_json_layer = folium.GeoJson(
    geo_df2.to_json(),
    style_function=style_function,
    #highlight_function={'fillColor': 'yellow', 'fillOpacity': 0.2},
    name='DAC Classification'
).add_to(m)

# Add the GeoJSON layer to the map
folium.LayerControl().add_to(m)


#m.save(f'{parent_dir}/Static/original_map.html')

# Display the map
m

In [89]:
# Modify Marker template to include the onClick event
click_template = """{% macro script(this, kwargs) %}
    var {{ this.get_name() }} = L.marker(
        {{ this.location|tojson }},
        {{ this.options|tojson }}
    ).addTo({{ this._parent.get_name() }}).on('click', onClick);
{% endmacro %}"""

# Change template to custom template
Marker._template = Template(click_template)

location_center = [51.7678, -0.00675564]
m = folium.Map(location_center, zoom_start=13)

# Create the onClick listener function as a branca element and add to the map html
click_js = """function onClick(e) {
                 var point = e.latlng; alert(point)
                 }"""
                 
e = folium.Element(click_js)
html = m.get_root()
html.script.get_root().render()
html.script._children[e.get_name()] = e

#Add marker (click on map an alert will display with latlng values)
marker = folium.Marker([51.7678, -0.00675564]).add_to(m)
m.save('map_onlcick1.html')

In [93]:
m = folium.Map(location=[45.5236, -122.6750], zoom_start=13)
custom_js = '''
function onMapClick(e) {
    alert("You clicked the map at " + e.latlng);
}

var map = this; // Ensure the map object is correctly referenced
map.on('click', onMapClick);
'''

class CustomJs(MacroElement):
    _template = Template(u"""
        {% macro script(this, kwargs) %}
        var map = {{this._parent.get_name()}};
        {{this.function}};
        {% endmacro %}
    """)

    def __init__(self, function):
        super(CustomJs, self).__init__()
        self.function = function



m.get_root().add_child(CustomJs(custom_js))

m.save('map_onlcick2.html')


In [97]:
m = folium.Map(location=[45.5236, -122.6750], zoom_start=13)

# Define the custom JavaScript code
custom_js = '''
function onMapClick(e) {
    var lat = e.latlng.lat;
    var lng = e.latlng.lng;
    window.ReactNativeWebView.postMessage(JSON.stringify({ lat: lat, lng: lng }));
}

var map = this; // Ensure the map object is correctly referenced
map.on('click', onMapClick);
'''

class CustomJs(MacroElement):
    _template = Template(u"""
        {% macro script(this, kwargs) %}
        var map = {{this._parent.get_name()}};
        {{this.function}};
        {% endmacro %}
    """)

    def __init__(self, function):
        super(CustomJs, self).__init__()
        self.function = function

# Add the custom JavaScript to the map
m.get_root().add_child(CustomJs(custom_js))
m.save('map_onlcick.html')

In [102]:
m = folium.Map(location=[45.5236, -122.6750], zoom_start=13)

# Define the custom JavaScript code
custom_js = '''
function onMapClick(e) {
    var lat = e.latlng.lat;
    var lng = e.latlng.lng;
    window.parent.postMessage(JSON.stringify({ lat: lat, lng: lng }), '*');
}

var map = this; // Ensure the map object is correctly referenced
map.on('click', onMapClick);
'''

class CustomJs(MacroElement):
    _template = Template(u"""
        {% macro script(this, kwargs) %}
        var map = this;
        {{this.function}};
        {% endmacro %}
    """)

    def __init__(self, function):
        super(CustomJs, self).__init__()
        self.function = function

# Add the custom JavaScript to the map
m.get_root().add_child(CustomJs(custom_js))
m.save('map_onlcick.html')